# DuckDB Spatial



## このノートブックの流れ

- 生成 AI に、自然言語から SQL を出力させる
- 出力された SQL を DuckDB で実行する
- 実行結果を GeoJSON に変換する
- GeoJSON を地図上に表示する

## 前準備

### 出力を大きく表示する関数の用意

In [1]:
from IPython.display import Markdown, display
def print_large(text):
    display(Markdown(f"### {text}"))

## DuckDB のセットアップとデータの読み込み

In [ ]:
import duckdb
import requests
import json

# GeoJSONファイルのURL
geojson_url = "https://github.com/nvkelso/natural-earth-vector/raw/master/geojson/ne_110m_admin_0_countries.geojson"
# geojson_url = "https://github.com/nvkelso/natural-earth-vector/raw/master/geojson/ne_10m_admin_0_countries.geojson"

try:
    # DuckDBに読み込む
    conn = duckdb.connect()
    conn.execute("""
    INSTALL httpfs;
    INSTALL json;
    INSTALL spatial;
    """)
    conn.execute(f"""
    LOAD httpfs;
    LOAD json;
    LOAD spatial;
    CREATE TABLE countries AS SELECT * FROM ST_Read('{geojson_url}')
    """)

    # NOTE: closeするとDBの内容が失われるのでcloseしてはいけない
    # conn.close()
except requests.exceptions.RequestException as e:
    print(f"Error downloading GeoJSON: {e}")
except json.JSONDecodeError as e:
    print(f"Error decoding JSON: {e}")
except Exception as e:
    print(f"An unexpected error occurred: {e}")

FloatProgress(value=0.0, layout=Layout(width='auto'), style=ProgressStyle(bar_color='black'))

## データベースのテーブルスキーマを文字列にする

In [3]:
try:
    # NOTE: connはgeojsonを読み込んだものを使い回す必要がある
    # conn = duckdb.connect()
    summary_of_tables = ""

    # SHOWによってテーブル一覧を取得
    show_result = conn.execute("SHOW").fetchall()
    tables = [row[2] for row in show_result]

    for table in tables:
        summary_of_tables += f"Table: {table}\n"
        # DESCRIBE TABLEの結果を文字列に変換
        describe_result = conn.execute(f"DESCRIBE TABLE {table}").fetchall()
        for row in describe_result:
            field_name = row[0]
            field_type = row[1]
            summary_of_tables += f"  Field: {field_name}, {field_type}\n"
    print(summary_of_tables)
except Exception as e:
    print(f"An unexpected error occurred: {e}")

Table: countries
  Field: featurecla, VARCHAR
  Field: scalerank, INTEGER
  Field: LABELRANK, INTEGER
  Field: SOVEREIGNT, VARCHAR
  Field: SOV_A3, VARCHAR
  Field: ADM0_DIF, INTEGER
  Field: LEVEL, INTEGER
  Field: TYPE, VARCHAR
  Field: TLC, VARCHAR
  Field: ADMIN, VARCHAR
  Field: ADM0_A3, VARCHAR
  Field: GEOU_DIF, INTEGER
  Field: GEOUNIT, VARCHAR
  Field: GU_A3, VARCHAR
  Field: SU_DIF, INTEGER
  Field: SUBUNIT, VARCHAR
  Field: SU_A3, VARCHAR
  Field: BRK_DIFF, INTEGER
  Field: NAME, VARCHAR
  Field: NAME_LONG, VARCHAR
  Field: BRK_A3, VARCHAR
  Field: BRK_NAME, VARCHAR
  Field: BRK_GROUP, VARCHAR
  Field: ABBREV, VARCHAR
  Field: POSTAL, VARCHAR
  Field: FORMAL_EN, VARCHAR
  Field: FORMAL_FR, VARCHAR
  Field: NAME_CIAWF, VARCHAR
  Field: NOTE_ADM0, VARCHAR
  Field: NOTE_BRK, VARCHAR
  Field: NAME_SORT, VARCHAR
  Field: NAME_ALT, VARCHAR
  Field: MAPCOLOR7, INTEGER
  Field: MAPCOLOR8, INTEGER
  Field: MAPCOLOR9, INTEGER
  Field: MAPCOLOR13, INTEGER
  Field: POP_EST, DOUBLE
  Fie

## 対象となる自然言語

In [4]:
input_text = "世界で一番広い国は？"
print_large(input_text)

### 世界で一番広い国は？

## 生成 AI にスキーマと自然言語から SQL を出力させる

In [5]:
from langchain_core.prompts import ChatPromptTemplate
from langchain_google_genai import ChatGoogleGenerativeAI

# モデルの準備
model = ChatGoogleGenerativeAI(model="gemini-exp-1206", temperature=0)

# プロンプトの準備
template = """You are an expert of PostgreSQL and PostGIS.
You output the best PostgreSQL query based on given table schema and input text.

You will always reply according to the following rules:
- Output valid PostgreSQL query.
- The query MUST be return name, value and geom columns. Use AS to rename columns.
- The query MUST use ST_AsGeoJSON function to output geom column.
- The query MUST be line delimited and surrounded by just three backquote to indicate that it is a code block.

** Table Schema: **
{table_schema}

User Input:
{input}
"""
prompt = ChatPromptTemplate.from_template(template)

chain = prompt | model

res = chain.invoke({"input": input_text, "table_schema": summary_of_tables})
result = res.content.strip()
print(result)

```sql
SELECT
  NAME AS name,
  ST_Area(geom) AS value,
  ST_AsGeoJSON(geom) AS geom
FROM countries
ORDER BY
  value DESC
LIMIT 1;
```


In [6]:
import re
match = re.search(r"```[^\n]*\n(.*?)```", result, re.DOTALL)

if match:
    query = match.group(1).strip()
    print(query)
else:
    print("SQLが見つかりませんでした。")

SELECT
  NAME AS name,
  ST_Area(geom) AS value,
  ST_AsGeoJSON(geom) AS geom
FROM countries
ORDER BY
  value DESC
LIMIT 1;


## 出力された SQL を DuckDB で実行する

In [7]:
duckdb_result = conn.execute(query).fetchall()
duckdb_result

[('Antarctica',
  6049.574691530632,
  '{"type":"MultiPolygon","coordinates":[[[[-51.730641,-82.062557],[-51.246897,-82.010675],[-50.763173,-81.958754],[-50.733388,-81.959568],[-50.557932,-81.993829],[-50.122418,-81.973126],[-49.686903,-81.952423],[-49.251389,-81.93172],[-48.815875,-81.911017],[-48.38036,-81.890313],[-48.2294,-81.918227],[-48.220082,-81.915623],[-48.206899,-81.898696],[-48.198883,-81.892836],[-48.188222,-81.891534],[-47.887685,-81.92197],[-47.431223,-81.917657],[-47.380442,-81.923517],[-47.344879,-81.950128],[-47.350819,-81.954848],[-47.361969,-81.966241],[-47.368153,-81.97031],[-47.263783,-81.969985],[-47.423736,-82.007501],[-47.584584,-82.02044],[-47.562001,-82.03753],[-47.527577,-82.047621],[-47.49059,-82.052341],[-47.460317,-82.05283],[-47.396311,-82.045017],[-47.363108,-82.044692],[-47.295522,-82.069513],[-47.255523,-82.072198],[-47.215199,-82.065688],[-47.175689,-82.053318],[-47.087026,-82.003676],[-47.055043,-81.993259],[-46.667124,-81.951511],[-46.279205,-81.90

## SQL の実行結果を GeoJSON に変換する

In [8]:
# duckdb_resultをGeoJSONに変換する

import json

def duckdb_result_to_geojson(duckdb_result):
    """Converts DuckDB query result to GeoJSON format.

    Args:
        duckdb_result: The result of a DuckDB query.  Assumes the query returns
        columns named 'name', 'value', and 'geom' where 'geom' is a GeoJSON
        geometry string.

    Returns:
        A GeoJSON FeatureCollection as a string, or None if the conversion fails.
    """
    geojson = {
        "type": "FeatureCollection",
        "features": []
    }

    for row in duckdb_result:
        try:
            name, value, geom_str = row  # Assuming the columns are in this order
            geom = json.loads(geom_str)  # Parse the geometry string as GeoJSON
            feature = {
                "type": "Feature",
                "geometry": geom,
                "properties": {
                    "name": name,
                    "value": value
                }
            }
            geojson["features"].append(feature)
        except (ValueError, TypeError, IndexError) as e:
            print(f"Error processing row {row}: {e}")
            return None  # Return None if any row fails
        except Exception as e:
            print(f"An unexpected error occurred: {e}")
            return None

    return json.dumps(geojson, indent=2)


# Example usage with the duckdb_result
geojson_output = duckdb_result_to_geojson(duckdb_result)

if geojson_output:
    print(geojson_output)
else:
    print("Failed to convert DuckDB result to GeoJSON.")

{
  "type": "FeatureCollection",
  "features": [
    {
      "type": "Feature",
      "geometry": {
        "type": "MultiPolygon",
        "coordinates": [
          [
            [
              [
                -51.730641,
                -82.062557
              ],
              [
                -51.246897,
                -82.010675
              ],
              [
                -50.763173,
                -81.958754
              ],
              [
                -50.733388,
                -81.959568
              ],
              [
                -50.557932,
                -81.993829
              ],
              [
                -50.122418,
                -81.973126
              ],
              [
                -49.686903,
                -81.952423
              ],
              [
                -49.251389,
                -81.93172
              ],
              [
                -48.815875,
                -81.911017
              ],
              [
          

## GeoJSON を地図上に表示する

In [9]:
import folium
import json

geojson_data = json.loads(geojson_output)

m = folium.Map(location=[0, 0], zoom_start=2)  # default map

# Add the GeoJSON data to the map
folium.GeoJson(geojson_data).add_to(m)

# Get bounds from GeoJSON data and fit the map to those bounds
# Extract bounds from geojson_data
bounds = folium.GeoJson(geojson_data).get_bounds()
# Ensure bounds are valid before fitting
if bounds:
    m.fit_bounds(bounds)

# Display the map
display(m)
